 # GJGNY Data Wrangling

In [1]:
import requests
import numpy as np
import pandas as pd
import pandas_profiling
import json
import os
import matplotlib.pyplot as plt

pd.options.display.max_columns = None

In [2]:
#imports csv
os.chdir(r'C:\Users\2bogu\Desktop\Sringboard_Materials\capstone2\data\external')

df = pd.read_csv('Green_Jobs_-_Green_New_York__GJGNY__Residential_Loan_Portfolio___Beginning_November_2010.csv')

#USE API WHEN?

In [3]:
df.dtypes

Reporting Period              object
CONTRACT DATE                 object
SETUP DATE                    object
ORIGINAL LOAN AMOUNT         float64
ORIGINAL TERM                  int64
ORIGINAL MATURITY DATE        object
CURRENT MATURITY DATE         object
INTEREST RATE                float64
CREDIT SCORE CURRENT HIGH    float64
CREDIT SCORE                 float64
CREDIT SCORE NAME 2          float64
DEBT TO INCOME               float64
FIRST PAYMENT DATE            object
LAST PAYMENT DATE             object
LAST PAYMENT AMOUNT          float64
NEXT PAYMENT DUE DATE         object
PAYMENT AMOUNT               float64
CURRENT BALANCE              float64
UNAPPLIED CASH               float64
DELINQUENT AMOUNT            float64
TOTAL INTEREST PAID          float64
TOTAL LATE CHARGE PAID       float64
PAYMENTS REMAINING             int64
DAYS DELINQUENT                int64
PROPERTY COUNTY               object
UTILITY                       object
INSTALLATION CITY             object
I

In [4]:
df.shape

(27385, 41)

In [5]:
df = df.drop_duplicates() #drops the one duplicate record

In [6]:
#df.shape
df['SUCCESSOR NUMBER'].value_counts()

S-1    334
S-0    322
S-2     53
s-1     29
S-3     19
S-4      4
s-2      2
s-3      2
S-5      2
S-6      2
s-0      1
Name: SUCCESSOR NUMBER, dtype: int64

# Change of plan

## New problem statment: How can the Residential Loan Porfoilio attract people that will get ahead of loan payments


New columns: is_ahead, single_borrower, avg_weekly_payment, avg_credit_score

Include incomplete loans? 

Predict: if applicant will get ahead, how much they will get ahead, probability that applicant will get ahead/ by year 1 or year 2 or ...


In [7]:
df.columns

Index(['Reporting Period', 'CONTRACT DATE', 'SETUP DATE',
       'ORIGINAL LOAN AMOUNT', 'ORIGINAL TERM', 'ORIGINAL MATURITY DATE',
       'CURRENT MATURITY DATE', 'INTEREST RATE', 'CREDIT SCORE CURRENT HIGH',
       'CREDIT SCORE', 'CREDIT SCORE NAME 2', 'DEBT TO INCOME',
       'FIRST PAYMENT DATE', 'LAST PAYMENT DATE', 'LAST PAYMENT AMOUNT',
       'NEXT PAYMENT DUE DATE', 'PAYMENT AMOUNT', 'CURRENT BALANCE',
       'UNAPPLIED CASH', 'DELINQUENT AMOUNT', 'TOTAL INTEREST PAID',
       'TOTAL LATE CHARGE PAID', 'PAYMENTS REMAINING', 'DAYS DELINQUENT',
       'PROPERTY COUNTY', 'UTILITY', 'INSTALLATION CITY', 'INSTALLATION ZIP',
       'Contractor Name', 'SUCCESSOR NUMBER', 'ACCOUNT CODE',
       'ACCOUNT CODE DATE', 'CANCEL REASON', 'TYPE OF BANKRUPTCY',
       'Months Since Origination', 'Payments Made', 'Purpose', 'Loan Type',
       'Underwriting', 'Pledged', 'Georeference'],
      dtype='object')

In [8]:
df = df.drop(['LAST PAYMENT AMOUNT', 'LAST PAYMENT DATE', 'FIRST PAYMENT DATE', 
              'DELINQUENT AMOUNT', 'DAYS DELINQUENT', 'Reporting Period', 
              'CREDIT SCORE CURRENT HIGH', 'NEXT PAYMENT DUE DATE', 'PAYMENTS REMAINING', 
              'PROPERTY COUNTY', 'UTILITY', 'INSTALLATION CITY', 'INSTALLATION ZIP', 
              'Contractor Name', 'Georeference', 'UNAPPLIED CASH', 'TOTAL LATE CHARGE PAID', 
              'Months Since Origination', 'CURRENT BALANCE'], axis=1)

In [9]:
df.columns

Index(['CONTRACT DATE', 'SETUP DATE', 'ORIGINAL LOAN AMOUNT', 'ORIGINAL TERM',
       'ORIGINAL MATURITY DATE', 'CURRENT MATURITY DATE', 'INTEREST RATE',
       'CREDIT SCORE', 'CREDIT SCORE NAME 2', 'DEBT TO INCOME',
       'PAYMENT AMOUNT', 'TOTAL INTEREST PAID', 'SUCCESSOR NUMBER',
       'ACCOUNT CODE', 'ACCOUNT CODE DATE', 'CANCEL REASON',
       'TYPE OF BANKRUPTCY', 'Payments Made', 'Purpose', 'Loan Type',
       'Underwriting', 'Pledged'],
      dtype='object')

In [10]:
report = df.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report

In [11]:
#new columns: 
#    difference between original maturity date and current maturity date,
#    time between contract and set up date
#    #num_borrowers,
#    average credit score

In [12]:
df['CREDIT SCORE'].mean()

734.5816394907304

In [13]:
#Missing: #CREDIT SCORE, CREDIT SCORE NAME 2, DEBT TO INCOME, #SUCCESSOR NUMBER, #CANCEL REASON,
#         #TYPE OF BANKRUPTY, 
#df['CREDIT SCORE NAME 2']

In [14]:
#CREATES NUM BORROWERS
df['num_borrowers'] = np.where(pd.notnull(df['CREDIT SCORE NAME 2']), 2, 1)

In [15]:
#FILLING CREDIT SCORE NAN WITH COLUMN AVG
cs_avg = df['CREDIT SCORE'].mean()
df['CREDIT SCORE'].fillna(int(cs_avg), inplace =True)
#df['CREDIT SCORE'] = df['CREDIT SCORE'].apply(lambda x: cs_avg if df['CREDIT SCORE'].isnull else x)
#FILLING IN CREDIT SCORE 2 TO CREATE AVG
#CREATES AVG CREDIT SCORE
df['CREDIT SCORE NAME 2'] = df['CREDIT SCORE NAME 2'].fillna(df['CREDIT SCORE'])
# creates average credit score for the account in one column
df['avg_credit_score'] = df[['CREDIT SCORE', 'CREDIT SCORE NAME 2']].mean(axis=1)
df.drop(['CREDIT SCORE', 'CREDIT SCORE NAME 2'], inplace=True, axis=1)

In [16]:
#df.info()

In [17]:
df['SUCCESSOR NUMBER'].fillna('NONE', inplace = True)

In [18]:
df['CANCEL REASON'].fillna('NONE', inplace = True)

In [19]:
df['TYPE OF BANKRUPTCY'].fillna('NONE', inplace = True)

In [20]:
#df.info()

In [21]:
# Avg of debt to income to replace nans
di_avg = df['DEBT TO INCOME'].mean()
df['DEBT TO INCOME'].fillna(int(di_avg), inplace =True)

In [22]:
#df.info()

In [23]:
df.to_csv(r'C:\Users\2bogu\Desktop\Sringboard_Materials\capstone2\data\interim\iter_avg', index = False)

In [24]:
# setting up df with dropped nans rather than replacing them with average
df = pd.read_csv('Green_Jobs_-_Green_New_York__GJGNY__Residential_Loan_Portfolio___Beginning_November_2010.csv')
df = df.drop(['LAST PAYMENT AMOUNT', 'LAST PAYMENT DATE', 'FIRST PAYMENT DATE', 
              'DELINQUENT AMOUNT', 'DAYS DELINQUENT', 'Reporting Period', 
              'CREDIT SCORE CURRENT HIGH', 'NEXT PAYMENT DUE DATE', 'PAYMENTS REMAINING', 
              'PROPERTY COUNTY', 'UTILITY', 'INSTALLATION CITY', 'INSTALLATION ZIP', 
              'Contractor Name', 'Georeference', 'UNAPPLIED CASH', 'TOTAL LATE CHARGE PAID', 
              'Months Since Origination', 'CURRENT BALANCE'], axis=1)
df['num_borrowers'] = np.where(pd.notnull(df['CREDIT SCORE NAME 2']), 2, 1)
df['CREDIT SCORE NAME 2'] = df['CREDIT SCORE NAME 2'].fillna(df['CREDIT SCORE'])
df['SUCCESSOR NUMBER'].fillna('NONE', inplace = True)
df['CANCEL REASON'].fillna('NONE', inplace = True)
df['TYPE OF BANKRUPTCY'].fillna('NONE', inplace = True)

In [25]:
#df.info()

In [26]:
df = df.dropna()

In [27]:
# gets avg credit score and removes two original columns
df['avg_credit_score'] = df[['CREDIT SCORE', 'CREDIT SCORE NAME 2']].mean(axis=1)
df.drop(['CREDIT SCORE', 'CREDIT SCORE NAME 2'], inplace=True, axis=1)

In [28]:
#df.info()

In [29]:
df.to_csv(r'C:\Users\2bogu\Desktop\Sringboard_Materials\capstone2\data\interim\iter_drop', index = False)